In [7]:
import pandas as pd
import geopandas as gpd
import folium
from folium.plugins import MarkerCluster
from IPython.display import display

In [8]:
df = pd.read_csv("../data/signals_markings_signs/signals_signs_markings_combined.csv")
df.head()

/var/folders/0q/f6wdygs95dz97f63ll8xv7mc0000gn/T/ipykernel_31087/1819727849.py:1: DtypeWarning: Columns (0,2,3,8,9,10,13,14,16,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,36,37,38,39,40,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,67,68,69,71,72,73,74,75,76,77,78,79,80,81,84,86,87,88,89) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("../data/signals_markings_signs/signals_signs_markings_combined.csv")


the_geom  BoroCode  BoroName BoroCD  \
0   POINT (-73.88872558605694 40.76890772856818)       4.0    Queens    480   
1    POINT (-73.8697005932744 40.73548873454497)       4.0    Queens    404   
2  POINT (-73.80951061170703 40.761290727553074)       4.0    Queens    407   
3   POINT (-73.85698059676126 40.74725973149692)       4.0    Queens    404   
4    POINT (-73.94935857589593 40.6092207617288)       3.0  Brooklyn    315   

   CounDist  AssemDist  StSenDist  CongDist                          Location  \
0      21.0       35.0       11.0      14.0  Ditmars Boulevard and  81 Street   
1      25.0       39.0       13.0       6.0          57 Avenue and  92 Street   
2      20.0       40.0       16.0       6.0     Sanford Avenue and 156 Street   
3      21.0       39.0       13.0       6.0         108 Street and  46 Avenue   
4      48.0       41.0       22.0       9.0  Quentin Road and East  24 Street   

    Borough  ...  ref  addr_housenumber  addr_postcode addr_street layer  \
0    Queens  ...  NaN               NaN            NaN         NaN   NaN   
1    Queens  ...  NaN               NaN            NaN         NaN   NaN   
2    Queens  ...  NaN               NaN            NaN         NaN   NaN   
3    Queens  ...  NaN               NaN            NaN         NaN   NaN   
4  Brooklyn  ...  NaN               NaN            NaN         NaN   NaN   

   tunnel road_marking historic turn_lanes_forward ObjectId  
0     NaN          NaN      NaN                NaN      NaN  
1     NaN          NaN      NaN                NaN      NaN  
2     NaN          NaN      NaN                NaN      NaN  
3     NaN          NaN      NaN                NaN      NaN  
4     NaN          NaN      NaN                NaN      NaN  

[5 rows x 91 columns]

In [9]:
print("\nCount of entries by source:")
print(df["source"].value_counts())


✅ Count of entries by source:
source
street_sign              7007106
traffic_signal             11200
accessible_ped_signal       3343
Name: count, dtype: int64


In [10]:
# Inspect column names
print("\nAvailable columns:", df.columns.tolist())

# View some entries from the street_sign dataset
street_signs = df[df["source"] == "street_sign"]
street_signs.head()


Available columns: ['the_geom', 'BoroCode', 'BoroName', 'BoroCD', 'CounDist', 'AssemDist', 'StSenDist', 'CongDist', 'Location', 'Borough', 'Date_Insta', 'POINT_X', 'POINT_Y', 'FEMAFldz', 'FEMAFldT', 'HrcEvac', 'NTAname', 'source', 'order_number', 'record_type', 'order_type', 'borough', 'on_street', 'on_street_suffix', 'from_street', 'from_street_suffix', 'to_street', 'to_street_suffix', 'side_of_street', 'order_completed_on_date', 'sign_code', 'sign_description', 'sign_size', 'sign_design_voided_on_date', 'sign_location', 'distance_from_intersection', 'arrow_direction', 'facing_direction', 'sheeting_type', 'support', 'sign_notes', 'sign_x_coord', 'sign_y_coord', 'X', 'Y', 'F_id', 'highway', 'direction', 'traffic_signals_direction', 'traffic_signals', 'crossing', 'kerb', 'button_operated', 'traffic_signals_sound', 'traffic_signals_vibration', 'tactile_paving', 'day_off', 'day_on', 'hour_off', 'hour_on', 'bicycle', 'name', 'name_es', 'note', 'photo', 'side', 'asset_ref', 'route_ref', 's

the_geom  BoroCode BoroName BoroCD  CounDist  AssemDist  StSenDist  \
3343      NaN       NaN      NaN    NaN       NaN        NaN        NaN   
3344      NaN       NaN      NaN    NaN       NaN        NaN        NaN   
3345      NaN       NaN      NaN    NaN       NaN        NaN        NaN   
3346      NaN       NaN      NaN    NaN       NaN        NaN        NaN   
3347      NaN       NaN      NaN    NaN       NaN        NaN        NaN   

      CongDist Location Borough  ...  ref  addr_housenumber  addr_postcode  \
3343       NaN      NaN     NaN  ...  NaN               NaN            NaN   
3344       NaN      NaN     NaN  ...  NaN               NaN            NaN   
3345       NaN      NaN     NaN  ...  NaN               NaN            NaN   
3346       NaN      NaN     NaN  ...  NaN               NaN            NaN   
3347       NaN      NaN     NaN  ...  NaN               NaN            NaN   

     addr_street layer  tunnel road_marking historic turn_lanes_forward  \
3343         NaN   NaN     NaN          NaN      NaN                NaN   
3344         NaN   NaN     NaN          NaN      NaN                NaN   
3345         NaN   NaN     NaN          NaN      NaN                NaN   
3346         NaN   NaN     NaN          NaN      NaN                NaN   
3347         NaN   NaN     NaN          NaN      NaN                NaN   

     ObjectId  
3343      NaN  
3344      NaN  
3345      NaN  
3346      NaN  
3347      NaN  

[5 rows x 91 columns]

In [32]:
print("\nAvailable columns:", df.columns.tolist())

# View sample rows from APS
target = df[df["source"] == "accessible_ped_signal"].copy()
target["POINT_X"] = pd.to_numeric(target["POINT_X"], errors="coerce")
target["POINT_Y"] = pd.to_numeric(target["POINT_Y"], errors="coerce")
target = target.dropna(subset=["POINT_X", "POINT_Y"])
print("Valid APS points:", len(target))


Available columns: ['the_geom', 'BoroCode', 'BoroName', 'BoroCD', 'CounDist', 'AssemDist', 'StSenDist', 'CongDist', 'Location', 'Borough', 'Date_Insta', 'POINT_X', 'POINT_Y', 'FEMAFldz', 'FEMAFldT', 'HrcEvac', 'NTAname', 'source', 'order_number', 'record_type', 'order_type', 'borough', 'on_street', 'on_street_suffix', 'from_street', 'from_street_suffix', 'to_street', 'to_street_suffix', 'side_of_street', 'order_completed_on_date', 'sign_code', 'sign_description', 'sign_size', 'sign_design_voided_on_date', 'sign_location', 'distance_from_intersection', 'arrow_direction', 'facing_direction', 'sheeting_type', 'support', 'sign_notes', 'sign_x_coord', 'sign_y_coord', 'X', 'Y', 'F_id', 'highway', 'direction', 'traffic_signals_direction', 'traffic_signals', 'crossing', 'kerb', 'button_operated', 'traffic_signals_sound', 'traffic_signals_vibration', 'tactile_paving', 'day_off', 'day_on', 'hour_off', 'hour_on', 'bicycle', 'name', 'name_es', 'note', 'photo', 'side', 'asset_ref', 'route_ref', 's

In [33]:
# Create GeoDataFrame (assume coordinates are EPSG:4326)
gdf = gpd.GeoDataFrame(
    target,
    geometry=gpd.points_from_xy(target["POINT_X"], target["POINT_Y"]),
    crs="EPSG:4326"
)

# Create folium map
m = folium.Map(location=[40.7128, -74.0060], zoom_start=12, tiles="CartoDB positron")
marker_cluster = MarkerCluster().add_to(m)

# Add APS markers to the map
for _, row in gdf.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        popup=f"APS Location"
    ).add_to(marker_cluster)

# Show the map
display(m)


In [11]:
aps = df[df["source"] == "accessible_ped_signal"]
print("Accessible Pedestrian Signals Count:", len(aps))

Accessible Pedestrian Signals Count: 3343


In [12]:
signals = df[df["source"] == "traffic_signal"]
signals["X"] = pd.to_numeric(signals["X"], errors="coerce")
signals["Y"] = pd.to_numeric(signals["Y"], errors="coerce")

signals.describe()[["X", "Y"]]


/var/folders/0q/f6wdygs95dz97f63ll8xv7mc0000gn/T/ipykernel_31087/1286258282.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  signals["X"] = pd.to_numeric(signals["X"], errors="coerce")
/var/folders/0q/f6wdygs95dz97f63ll8xv7mc0000gn/T/ipykernel_31087/1286258282.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  signals["Y"] = pd.to_numeric(signals["Y"], errors="coerce")


X             Y
count  1.120000e+04  1.120000e+04
mean  -8.226036e+06  4.968834e+06
std    8.781281e+03  7.393858e+03
min   -8.236928e+06  4.952727e+06
25%   -8.233231e+06  4.963594e+06
50%   -8.228677e+06  4.969146e+06
75%   -8.219945e+06  4.974885e+06
max   -8.204410e+06  4.982973e+06

In [13]:
# Normalize coordinates across all sources
df_coords = df.copy()

df_coords.loc[df_coords["source"] == "accessible_ped_signal", "POINT_X"] = df_coords["POINT_X"]
df_coords.loc[df_coords["source"] == "accessible_ped_signal", "POINT_Y"] = df_coords["POINT_Y"]

df_coords.loc[df_coords["source"] == "street_sign", "POINT_X"] = df_coords["sign_x_coord"]
df_coords.loc[df_coords["source"] == "street_sign", "POINT_Y"] = df_coords["sign_y_coord"]

df_coords.loc[df_coords["source"] == "traffic_signal", "POINT_X"] = df_coords["X"]
df_coords.loc[df_coords["source"] == "traffic_signal", "POINT_Y"] = df_coords["Y"]

df_coords["POINT_X"] = pd.to_numeric(df_coords["POINT_X"], errors="coerce")
df_coords["POINT_Y"] = pd.to_numeric(df_coords["POINT_Y"], errors="coerce")

all_points = df_coords.dropna(subset=["POINT_X", "POINT_Y"]).copy()
print("Unified coordinate entries available:", len(all_points))

Unified coordinate entries available: 7021649


In [17]:
import geopandas as gpd
import folium
from folium.plugins import MarkerCluster
from IPython.display import display

# Create GeoDataFrame
# Treat coordinates as EPSG:2263 and convert to WGS84
gdf = gpd.GeoDataFrame(
    all_points,
    geometry=gpd.points_from_xy(all_points["POINT_X"], all_points["POINT_Y"]),
    crs="EPSG:2263"  # this is crucial!
).to_crs("EPSG:4326")  # convert to latitude/longitude

# Sample 1000 random points for smoother map rendering
gdf_sample = gdf.sample(n=1000, random_state=42)

# Create map
m = folium.Map(location=[40.7128, -74.0060], zoom_start=12, tiles="CartoDB positron")
marker_cluster = MarkerCluster().add_to(m)

# Add sampled points to the map
for _, row in gdf_sample.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        popup=f"Source: {row['source']}"
    ).add_to(marker_cluster)

display(m)

In [19]:
from datamart_profiler import process_dataset
import json

input_path = "../data/signals_markings_signs/signals_signs_markings_combined.csv"
output_path = "../data_profiles/signals_markings_signs.json"

# Generate the profile and save to JSON
profile_result = process_dataset(input_path)
with open(output_path, "w") as f:
    json.dump(profile_result, f, indent=2)

print(f"Profile saved to: {output_path}")

Profile saved to: ../data_profiles/signals_markings_signs.json
